In [129]:
!python3 -m pip install --upgrade pip
!python3 -m pip install torch torchvision
!python3 -m pip install rasterio
!python3 -m pip install git+https://github.com/PatBall1/detectree2.git
!python3 -m pip install opencv-python
!python3 -m pip install --upgrade pygeos

  Cloning https://github.com/PatBall1/detectree2.git to /private/var/folders/ry/qhyv3_sd28n3rzthk9tzgl5r0000gn/T/pip-req-build-pegzj7hz
  Running command git clone --filter=blob:none --quiet https://github.com/PatBall1/detectree2.git /private/var/folders/ry/qhyv3_sd28n3rzthk9tzgl5r0000gn/T/pip-req-build-pegzj7hz
  Resolved https://github.com/PatBall1/detectree2.git to commit 2f29886bafcb63743a7f3ab596c5c3796ca4a243
  Preparing metadata (setup.py) ... done
  Cloning https://github.com/facebookresearch/detectron2.git to /private/var/folders/ry/qhyv3_sd28n3rzthk9tzgl5r0000gn/T/pip-install-fwk5zu1m/detectron2_12d9700015c04059b996ce7d379fb3bf
  Running command git clone --filter=blob:none --quiet https://github.com/facebookresearch/detectron2.git /private/var/folders/ry/qhyv3_sd28n3rzthk9tzgl5r0000gn/T/pip-install-fwk5zu1m/detectron2_12d9700015c04059b996ce7d379fb3bf
  Resolved https://github.com/facebookresearch/detectron2.git to commit 79f914785a87b80565381f4489b129e633c4efb5
  Preparing m

In [386]:
import torch
import torchvision
import rasterio
import detectree2
from detectree2.preprocessing.tiling import tile_data
from detectree2.models.outputs import project_to_geojson, stitch_crowns, clean_crowns
from detectree2.models.predict import predict_on_data
from detectree2.models.train import setup_cfg
from detectron2.engine import DefaultPredictor
import cv2
import os
from osgeo import gdal
import shutil
import numpy as np
import geopandas as gpd
import pandas as pd
from pathlib import Path
from shapely.geometry import Polygon, box, shape
from rasterio.crs import CRS
import os
from datetime import datetime, timedelta
from os.path import join
from shapely.ops import unary_union
import math

In [31]:
def clear_directory(directory):
    """Remove all files in the specified directory."""
    if os.path.exists(directory):
        for filename in os.listdir(directory):
            file_path = os.path.join(directory, filename)
            if os.path.isfile(file_path) or os.path.islink(file_path):
                os.unlink(file_path)
            elif os.path.isdir(file_path):
                shutil.rmtree(file_path)

In [32]:
def resample_raster(input_raster, match_raster, output_raster):
    """
    Resample input_raster to match the dimensions, extent, and projection of match_raster.
    """
    src_ds = gdal.Open(input_raster)
    match_ds = gdal.Open(match_raster)
    
    # Get the driver for the output format
    driver = gdal.GetDriverByName('GTiff')
    
    # Create the output dataset with the same dimensions as the match dataset
    out_ds = driver.Create(
        output_raster,
        match_ds.RasterXSize,
        match_ds.RasterYSize,
        1,
        gdal.GDT_Float32
    )
    
    # Set the geotransform and projection from the match dataset
    out_ds.SetGeoTransform(match_ds.GetGeoTransform())
    out_ds.SetProjection(match_ds.GetProjection())
    
    # Perform the resampling
    gdal.ReprojectImage(
        src_ds,
        out_ds,
        src_ds.GetProjection(),
        match_ds.GetProjection(),
        gdal.GRA_Bilinear
    )
    
    # Close the datasets
    out_ds = None
    src_ds = None
    match_ds = None

In [33]:
def filter_tiles(output_folder):
    """Filter out tiles that are all black."""
    for filename in os.listdir(output_folder):
        file_path = os.path.join(output_folder, filename)
        if file_path.endswith('.tif'):
            with rasterio.open(file_path) as src:
                tile_data = src.read(1)
                # Check if the tile is all black
                print(tile_data)
                print(np.all(tile_data <= -9999))
                if np.all(tile_data <= -9999):
                    os.remove(file_path)

In [389]:
def create_chm_tiles_nob(dsm_path, dem_resampled_path, output_folder, num_tiles, x, y):
    # Open the DSM and resampled DEM files
    dsm_ds = gdal.Open(dsm_path)
    dem_ds = gdal.Open(dem_resampled_path)
    
    nx = int(math.sqrt(num_tiles / 2))
    ny = nx * 2

    # Ensure that the total number of tiles meets the requirement, adjust if not
    if nx * ny != num_tiles:
        print(f"Warning: The number of tiles ({nx} x {ny}) does not match the specified number of tiles ({num_tiles}).")

    # Calculate tile sizes based on the number of tiles in each direction
    tile_x_size = dsm_ds.RasterXSize // nx
    tile_y_size = dsm_ds.RasterYSize // ny


    shift_x = 0
    if ( x ):
        shift_x = tile_x_size // 2
    shift_y = 0
    if ( y ):
        shift_y = tile_y_size // 2

    clear_directory(output_folder)
    
    for i in range(shift_x, dsm_ds.RasterXSize, tile_x_size):
        for j in range(shift_y, dsm_ds.RasterYSize, tile_y_size):
            width = min(tile_x_size, dsm_ds.RasterXSize - i)
            height = min(tile_y_size, dsm_ds.RasterYSize - j)
            
            dsm_data = dsm_ds.GetRasterBand(1).ReadAsArray(i, j, width, height)
            dem_data = dem_ds.GetRasterBand(1).ReadAsArray(i, j, width, height)
            chm_data = dsm_data - dem_data
            
            output_path = os.path.join(output_folder, f"chm_tile_{i}_{j}.tif")
            driver = gdal.GetDriverByName('GTiff')
            out_ds = driver.Create(output_path, width, height, 1, gdal.GDT_Float32)
            out_ds.SetGeoTransform([
                dsm_ds.GetGeoTransform()[0] + i * dsm_ds.GetGeoTransform()[1],
                dsm_ds.GetGeoTransform()[1],
                0,
                dsm_ds.GetGeoTransform()[3] + j * dsm_ds.GetGeoTransform()[5],
                0,
                dsm_ds.GetGeoTransform()[5]
            ])
            out_ds.SetProjection(dsm_ds.GetProjection())
            out_ds.GetRasterBand(1).WriteArray(chm_data)
            out_ds.GetRasterBand(1).SetNoDataValue(-9999)
            out_ds = None


In [436]:
resample_raster('dem.tif', 'dsm.tif', 'dem_resampled.tif')

create_chm_tiles_nob('dsm.tif', 'dem_resampled.tif', 'chm_tiles_noshift', 98, False, False)
create_chm_tiles_nob('dsm.tif', 'dem_resampled.tif', 'chm_tiles_shiftx', 98, True, False)
create_chm_tiles_nob('dsm.tif', 'dem_resampled.tif', 'chm_tiles_shifty', 98, False, True)
create_chm_tiles_nob('dsm.tif', 'dem_resampled.tif', 'chm_tiles_shiftxy', 98, True, True)

filter_tiles('chm_tiles_noshift')
filter_tiles('chm_tiles_shiftx')
filter_tiles('chm_tiles_shifty')
filter_tiles('chm_tiles_shiftxy')


[[    15.740746      15.7705345     15.7769165 ... -10039.047
  -10039.044     -10039.039    ]
 [    15.770695      15.764835      15.766926  ... -10039.056
  -10039.053     -10039.047    ]
 [    15.767426      15.763241      15.735085  ... -10039.063
  -10039.061     -10039.056    ]
 ...
 [    23.00415       22.979103      22.953033  ... -10037.927
  -10037.93      -10037.933    ]
 [    23.01458       22.990456      22.967804  ... -10037.924
  -10037.925     -10037.927    ]
 [    23.021263      23.001232      22.981167  ... -10037.919
  -10037.921     -10037.923    ]]
False
[[-9999. -9999. -9999. ... -9999. -9999. -9999.]
 [-9999. -9999. -9999. ... -9999. -9999. -9999.]
 [-9999. -9999. -9999. ... -9999. -9999. -9999.]
 ...
 [-9999. -9999. -9999. ... -9999. -9999. -9999.]
 [-9999. -9999. -9999. ... -9999. -9999. -9999.]
 [-9999. -9999. -9999. ... -9999. -9999. -9999.]]
True
[[-9999. -9999. -9999. ... -9999. -9999. -9999.]
 [-9999. -9999. -9999. ... -9999. -9999. -9999.]
 [-9999. -9999.

In [199]:

def parse_filename(filename):
    # Extracts the x and y coordinates from the filename
    parts = filename.split('_')
    x = int(parts[2])  # Assuming 'chm_tile_0_0_crowns.geojson' format
    y = int(parts[3])
    return x, y

def load_tiles(folder_path):
    tiles = []
    for filename in os.listdir(folder_path):
        if filename.endswith('.geojson'):
            x, y = parse_filename(filename)
            tiles.append((x, y, filename))
    return tiles


def load_geojson(filepath):
    gdf = gpd.read_file(filepath)
    if gdf.crs is None:
        gdf.set_crs('epsg:32650', inplace=True)  # Set to a default CRS if it's missing
    return gdf


def load_all_polygons(folder_path):
    """Load all polygons from all GeoJSON files in the specified folder."""
    all_polygons = []
    for filename in os.listdir(folder_path):
        if filename.endswith('.geojson'):
            filepath = os.path.join(folder_path, filename)
            gdf = gpd.read_file(filepath)
            if gdf.crs is None:
                gdf.set_crs('epsg:32650', inplace=True)
            gdf['file_path'] = filepath  # Store the filepath within the GeoDataFrame
            all_polygons.append(gdf)
    return pd.concat(all_polygons).reset_index(drop=True)





In [437]:
data = load_all_polygons('result_polygons_noshift')
data.to_file('result_polygons_noshift.shp')
data = load_all_polygons('result_polygons_shifty')
data.to_file('result_polygons_shifty.shp')
data = load_all_polygons('result_polygons_shiftx')
data.to_file('result_polygons_shiftx.shp')